In [1]:
import os
import yaml
import shutil
from pathlib import Path
from datetime import datetime

import torch
from tqdm import tqdm
from ultralytics import YOLO
from sklearn import model_selection

In [2]:
image_files = sorted(os.listdir("images"))
label_files = sorted(os.listdir("labels"))
train_images, valid_images, train_labels, valid_labels = (
    model_selection.train_test_split(image_files, label_files, test_size=0.1)
)

In [3]:
def create_folder(
    image_names: list[str],
    label_names: list[str],
    img_src_dir: str,
    label_src_dir: str,
    img_dest_dir: str,
    label_dest_dir: str,
):
    if os.path.exists(img_dest_dir) == True:
        shutil.rmtree(img_dest_dir)
    os.makedirs(img_dest_dir)

    if os.path.exists(label_dest_dir) == True:
        shutil.rmtree(label_dest_dir)
    os.makedirs(label_dest_dir)

    for i in tqdm(range(len(image_names))):
        img_path = Path(img_src_dir) / image_names[i]
        img_dest = Path(img_dest_dir) / image_names[i]
        if os.path.exists(img_dest) == False:
            shutil.copy(img_path, img_dest)

        label_path = Path(label_src_dir) / label_names[i]
        label_dest = Path(label_dest_dir) / label_names[i]
        if os.path.exists(label_dest) == False:
            shutil.copy(label_path, label_dest)

        assert img_path.stem == label_path.stem

In [4]:
create_folder(
    image_names=train_images,
    label_names=train_labels,
    img_src_dir="images",
    label_src_dir="labels",
    img_dest_dir="train/images",
    label_dest_dir="train/labels",
)

create_folder(
    image_names=valid_images,
    label_names=valid_labels,
    img_src_dir="images",
    label_src_dir="labels",
    img_dest_dir="valid/images",
    label_dest_dir="valid/labels",
)

100%|██████████| 77/77 [00:00<00:00, 1658.81it/s]


In [5]:
dict_file = {
    "train": f"{Path("./train").resolve()}",
    "val": f"{Path("./valid").resolve()}",
    "nc": 3,
    "names": {0: "circle", 1: "oval", 2: "teardrop"},
}

with open("data.yaml", "w") as f:
    yaml.dump(dict_file, f)

In [6]:
model = YOLO("yolov8n.pt")

In [7]:
epochs = 100
current_time = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")

model.train(
    data="data.yaml",
    name=f"glass-bottle_{current_time}",
    task="detect",
    epochs=epochs,
    val=True,
    resume=False,
)

Ultralytics YOLOv8.2.36 🚀 Python-3.12.3 torch-2.3.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4070 Ti SUPER, 16376MiB)
engine/trainer: task=detect, mode=train, model=yolov8n.pt, data=data.yaml, epochs=100, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=glass-bottle_2024-06-20_18-41-38, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=False, save_conf=False, save_crop=False, show_

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: ethancao (ethan_cao). Use `wandb login --relogin` to force relogin


Freezing layer 'model.22.dfl.conv.weight'
AMP: running Automatic Mixed Precision (AMP) checks with YOLOv8n...
AMP: checks passed ✅


train: Scanning /home/ethan/Python-Table/glass-bottle-mouth-detection/train/labels... 690 images, 0 backgrounds, 0 corrupt: 100%|██████████| 690/690 [00:00<00:00, 1406.59it/s]

train: New cache created: /home/ethan/Python-Table/glass-bottle-mouth-detection/train/labels.cache


...

                   all         77         77      0.999          1      0.995      0.893



100 epochs completed in 0.102 hours.
Optimizer stripped from runs/detect/glass-bottle_2024-06-20_18-41-38/weights/last.pt, 6.2MB
Optimizer stripped from runs/detect/glass-bottle_2024-06-20_18-41-38/weights/best.pt, 6.2MB

Validating runs/detect/glass-bottle_2024-06-20_18-41-38/weights/best.pt...
Ultralytics YOLOv8.2.36 🚀 Python-3.12.3 torch-2.3.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4070 Ti SUPER, 16376MiB)
Model summary (fused): 168 layers, 3006233 parameters, 0 gradients, 8.1 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 3/3 [00:00<00:00,  6.57it/s]


                   all         77         77      0.997          1      0.995      0.902
                circle         20         20      0.996          1      0.995      0.918
                  oval         21         21      0.998          1      0.995      0.917
              teardrop         36         36      0.998          1      0.995      0.872
Speed: 0.2ms preprocess, 0.8ms inference, 0.0ms loss, 1.2ms postprocess per image
Results saved to runs/detect/glass-bottle_2024-06-20_18-41-38


ultralytics.utils.metrics.DetMetrics object with attributes:

ap_class_index: array([0, 1, 2])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x7f081577a7b0>
curves: ['Precision-Recall(B)', 'F1-Confidence(B)', 'Precision-Confidence(B)', 'Recall-Confidence(B)']
curves_results: [[array([          0,    0.001001,    0.002002,    0.003003,    0.004004,    0.005005,    0.006006,    0.007007,    0.008008,    0.009009,     0.01001,    0.011011,    0.012012,    0.013013,    0.014014,    0.015015,    0.016016,    0.017017,    0.018018,    0.019019,     0.02002,    0.021021,    0.022022,    0.023023,
          0.024024,    0.025025,    0.026026,    0.027027,    0.028028,    0.029029,     0.03003,    0.031031,    0.032032,    0.033033,    0.034034,    0.035035,    0.036036,    0.037037,    0.038038,    0.039039,     0.04004,    0.041041,    0.042042,    0.043043,    0.044044,    0.045045,    0.046046,    0.047047,
          0.04